In [8]:
from collections import OrderedDict

import pandas as pd

import numpy as np

import torch

import torch.nn as nn

from torch.utils.data import Dataset, DataLoader

from torch.nn import functional as F
from torchsummary import summary


from plotly import express as px
from plotly import graph_objects as go
from plotly import subplots as sp


from sklearn.model_selection import train_test_split


import progressbar

import copy


In [9]:
data = pd.read_csv("train.csv", index_col="id").rename(
    columns={
        "FAVC": "Frequent consumption of high caloric food",
        "FCVC": "Frequency of consumption of vegetables",
        "NCP": "Number of main meals",
        "CAEC": "Consumption of food between meals",
        "CH2O": "Consumption of water daily",
        "SCC": "Calories consumption monitoring",
        "FAF": "Physical activity frequency",
        "TUE": "Time using technology devices",
        "CALC": "Consumption of alcohol",
        "MTRANS": "Transportation used",
    }
)

data = pd.concat(
    [
        data[data["NObeyesdad"] == value].sample(2400)
        for value in data["NObeyesdad"].unique().tolist()
    ]
)


In [10]:
px.histogram(
    data,
    x="NObeyesdad",
)


In [11]:
data = data.assign(
    **{
        "Age": data.Age.round(),
        "Height": (data.Height * 100).round(),
        "Weight": data.Weight.round(),
        "Frequency of consumption of vegetables": data[
            "Frequency of consumption of vegetables"
        ]
        .round()
        .astype("int"),
        "Number of main meals": data["Number of main meals"].round().astype("int"),
        "Consumption of water daily": 8
        * data["Consumption of water daily"].round().astype("int"),
        "Physical activity frequency": data["Physical activity frequency"]
        .round()
        .astype("int"),
        "Time using technology devices": data["Time using technology devices"]
        .round()
        .astype("int"),
        "BMI": lambda x: x["Weight"]
        / x["Height"]
        / np.where(
            x["Physical activity frequency"] == 0,
            1,
            x["Physical activity frequency"],
        ),
    }
)


In [12]:
data.describe()


Age        Height        Weight   
count  16800.000000  16800.000000  16800.000000  \
mean      23.748631    170.003869     84.850298   
std        5.894450      8.817301     25.639355   
min       14.000000    145.000000     39.000000   
25%       20.000000    163.000000     65.000000   
50%       22.000000    170.000000     82.000000   
75%       26.000000    176.000000    106.000000   
max       61.000000    198.000000    165.000000   

       Frequency of consumption of vegetables  Number of main meals   
count                            16800.000000          16800.000000  \
mean                                 2.412679              2.741667   
std                                  0.564433              0.756929   
min                                  1.000000              1.000000   
25%                                  2.000000              3.000000   
50%                                  2.000000              3.000000   
75%                                  3.000000              3.000000   
max                                  3.000000              4.000000   

       Consumption of water daily  Physical activity frequency   
count                16800.000000                 16800.000000  \
mean                    16.232381                     1.017857   
std                      5.362400                     0.865661   
min                      8.000000                     0.000000   
25%                     16.000000                     0.000000   
50%                     16.000000                     1.000000   
75%                     16.000000                     2.000000   
max                     24.000000                     3.000000   

       Time using technology devices           BMI  
count                   16800.000000  16800.000000  
mean                        0.637500      0.427937  
std                         0.666852      0.178196  
min                         0.000000      0.075581  
25%                         0.000000      0.283400  
50%                         1.000000      0.431663  
75%                         1.000000      0.586592  
max                         2.000000      0.953757

In [13]:
data.info()


<class 'pandas.core.frame.DataFrame'>
Index: 16800 entries, 20039 to 6228
Data columns (total 18 columns):
 #   Column                                     Non-Null Count  Dtype  
---  ------                                     --------------  -----  
 0   Gender                                     16800 non-null  object 
 1   Age                                        16800 non-null  float64
 2   Height                                     16800 non-null  float64
 3   Weight                                     16800 non-null  float64
 4   family_history_with_overweight             16800 non-null  object 
 5   Frequent consumption of high caloric food  16800 non-null  object 
 6   Frequency of consumption of vegetables     16800 non-null  int32  
 7   Number of main meals                       16800 non-null  int32  
 8   Consumption of food between meals          16800 non-null  object 
 9   SMOKE                                      16800 non-null  object 
 10  Consumption of water dai

In [14]:
data.head()


Gender   Age  Height  Weight family_history_with_overweight   
id                                                                   
20039  Female  24.0   158.0    80.0                            yes  \
5079     Male  34.0   170.0    85.0                            yes   
2500   Female  22.0   173.0    78.0                            yes   
12462    Male  21.0   165.0    78.0                            yes   
13968    Male  18.0   170.0    80.0                            yes   

      Frequent consumption of high caloric food   
id                                                
20039                                       yes  \
5079                                        yes   
2500                                        yes   
12462                                        no   
13968                                       yes   

       Frequency of consumption of vegetables  Number of main meals   
id                                                                    
20039                                       2                     3  \
5079                                        2                     3   
2500                                        2                     2   
12462                                       2                     1   
13968                                       3                     3   

      Consumption of food between meals SMOKE  Consumption of water daily   
id                                                                          
20039                         Sometimes    no                          16  \
5079                          Sometimes    no                           8   
2500                          Sometimes    no                          16   
12462                        Frequently    no                          24   
13968                         Sometimes    no                          16   

      Calories consumption monitoring  Physical activity frequency   
id                                                                   
20039                              no                            1  \
5079                               no                            1   
2500                               no                            1   
12462                              no                            1   
13968                              no                            1   

       Time using technology devices Consumption of alcohol   
id                                                            
20039                              0              Sometimes  \
5079                               1                     no   
2500                               0              Sometimes   
12462                              0                     no   
13968                              1             Frequently   

         Transportation used           NObeyesdad       BMI  
id                                                           
20039  Public_Transportation  Overweight_Level_II  0.506329  
5079              Automobile  Overweight_Level_II  0.500000  
2500   Public_Transportation  Overweight_Level_II  0.450867  
12462  Public_Transportation  Overweight_Level_II  0.472727  
13968  Public_Transportation  Overweight_Level_II  0.470588

In [15]:
# Made a key that I can use to identify the labels once I convert them to their respective index.
label_values = data.NObeyesdad.unique().tolist()


In [7]:
# Feature engineered data

updated_data = (
    pd.get_dummies(
        data.select_dtypes("object").drop(columns=["NObeyesdad"]), drop_first=True
    )
    .join(data.select_dtypes("number"))
    .join(data["NObeyesdad"].apply(label_values.index))
)


In [16]:
px.scatter_matrix(updated_data, color="NObeyesdad", height=5000, width=5000)
